In [1]:
import maboss
import ginsim
import pandas as pd 
import numpy as np
import mygene

from create_generic_models.create_generic_patients_cfgs import create_generic_patients_cfg_bnd_validation


In [2]:
phenotype_data = pd.read_csv('data/TCGA_data/TCGA_GDC-PANCAN_tumor_stage_phenotype.csv')
genes_data = pd.read_csv('data/TCGA_data/TCGA_GDC-PANCAN_genes.csv')
cnv_data = pd.read_csv('data/TCGA_data/TCGA-PANCAN_cnv.csv')
montagud_data = (
    pd.read_csv('data/Montagud_inter_nodes_data.csv', header=1)
    .loc[:, ['Target node', 'Interaction type', 'Source']])

In [3]:
montagud_nodes = list(set(montagud_data['Target node'].tolist() + montagud_data['Source'].tolist()))
montagud_nodes = [node for node in montagud_nodes if node != '0/1']
montagud_nodes = [node.upper() for node in montagud_nodes if isinstance(node, str)]
montagud_nodes.append('KRAS')
to_remove = ['RAS', 'FUSED_EVENT', 'NKX3_1', 'SPOP', 'AR_ERG']

montagud_nodes = [node for node in montagud_nodes if node not in to_remove]
montagud_nodes = list(set(montagud_nodes))

In [4]:
phenotype_data = phenotype_data.set_index('sample')
phenotype_data = phenotype_data.transpose()

cnv_data_ids = list(cnv_data.columns)[1:]
genes_data_ids = list(genes_data.columns)[1:]
phenotypes_data_ids = list(phenotype_data.columns)

common_ids = list(set(phenotypes_data_ids) & set(cnv_data_ids) & set(genes_data_ids))[:100]

phenotypes_data_filtered = phenotype_data[common_ids]

phenotypes_data_filtered = phenotypes_data_filtered.transpose()
print(phenotypes_data_filtered.head())

                 demographic.age_at_index demographic.created_datetime  \
sample                                                                   
TCGA-XF-A9SU-01A                     74.0                          NaN   
TCGA-PE-A5DE-01A                     41.0                          NaN   
TCGA-XF-A9SP-01A                     59.0                          NaN   
TCGA-K4-A54R-01A                     59.0                          NaN   
TCGA-DK-A3IN-01A                     72.0                          NaN   

                 demographic.days_to_birth demographic.days_to_death  \
sample                                                                 
TCGA-XF-A9SU-01A                  -27068.0                     182.0   
TCGA-PE-A5DE-01A                  -15216.0                       NaN   
TCGA-XF-A9SP-01A                  -21776.0                     454.0   
TCGA-K4-A54R-01A                  -21601.0                       NaN   
TCGA-DK-A3IN-01A                  -26562.0       

In [5]:
phenotypes_data_filtered = phenotypes_data_filtered["diagnoses.tumor_stage"]
print(phenotypes_data_filtered.head())

phenotypes_data_filtered = phenotypes_data_filtered.to_frame()

# create groups based on the stages
group_0 = ['stage 0']
group_1 = ['stage i', 'stage ia', 'stage ib']
group_2 = ['stage ii', 'stage iia', 'stage iib', 'stage iic']
group_3 = ['stage iii', 'stage iiia', 'stage iiib', 'stage iiic']
group_4 = ['stage iv', 'stage iva', 'stage ivb', 'stage ivc']

conditions = [
    phenotypes_data_filtered['diagnoses.tumor_stage'].isin(group_0),
    phenotypes_data_filtered['diagnoses.tumor_stage'].isin(group_1),
    phenotypes_data_filtered['diagnoses.tumor_stage'].isin(group_2),
    phenotypes_data_filtered['diagnoses.tumor_stage'].isin(group_3),
    phenotypes_data_filtered['diagnoses.tumor_stage'].isin(group_4) 
    ]
choices = ['Local Cancer', 'Early Stage', 'Larger Tumor', 'Advanced Local Speed', 'Metastatic']

phenotypes_data_filtered.loc[:,'Tumor Group'] = np.select(conditions, choices, default = '')

phenotypes_data_filtered = phenotypes_data_filtered.reset_index()


sample
TCGA-XF-A9SU-01A     stage iv
TCGA-PE-A5DE-01A    stage iia
TCGA-XF-A9SP-01A    stage iii
TCGA-K4-A54R-01A     stage ii
TCGA-DK-A3IN-01A    stage iii
Name: diagnoses.tumor_stage, dtype: object


In [6]:
phenotypes_data_filtered['Tumor Group'].value_counts()


Tumor Group
Larger Tumor            40
Advanced Local Speed    28
Metastatic              23
Early Stage              7
                         2
Name: count, dtype: int64

In [7]:
sampled_df = (
    phenotypes_data_filtered.groupby('Tumor Group', group_keys=False)
    .apply(lambda x: x.sample(n=min(len(x), 10), random_state=42))
)
print(sampled_df)


              sample diagnoses.tumor_stage           Tumor Group
74  TCGA-B6-A0IN-01A               stage x                      
14  TCGA-PK-A5HB-01A          not reported                      
38  TCGA-B6-A400-01A            stage iiia  Advanced Local Speed
97  TCGA-DK-AA6S-01A             stage iii  Advanced Local Speed
36  TCGA-CF-A1HR-01A             stage iii  Advanced Local Speed
93  TCGA-D8-A1X6-01A            stage iiia  Advanced Local Speed
2   TCGA-XF-A9SP-01A             stage iii  Advanced Local Speed
54  TCGA-K4-A5RI-01A             stage iii  Advanced Local Speed
66  TCGA-ZF-AA4W-01A             stage iii  Advanced Local Speed
94  TCGA-ZF-AA4U-01A             stage iii  Advanced Local Speed
51  TCGA-K4-A6FZ-01A             stage iii  Advanced Local Speed
55  TCGA-OR-A5LG-01A             stage iii  Advanced Local Speed
10  TCGA-BH-A0HU-01A              stage ia           Early Stage
22  TCGA-OR-A5L3-01A               stage i           Early Stage
62  TCGA-PK-A5HA-01A     

/var/folders/83/pqwsm5cn7vscbq8l3fnf30qr0000gn/T/ipykernel_28866/811706021.py:3: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda x: x.sample(n=min(len(x), 10), random_state=42))


In [8]:
sampled_df['Tumor Group'].value_counts()

Tumor Group
Advanced Local Speed    10
Larger Tumor            10
Metastatic              10
Early Stage              7
                         2
Name: count, dtype: int64

In [9]:
samples_ids = list(sampled_df['sample'])
print(samples_ids)

['TCGA-B6-A0IN-01A', 'TCGA-PK-A5HB-01A', 'TCGA-B6-A400-01A', 'TCGA-DK-AA6S-01A', 'TCGA-CF-A1HR-01A', 'TCGA-D8-A1X6-01A', 'TCGA-XF-A9SP-01A', 'TCGA-K4-A5RI-01A', 'TCGA-ZF-AA4W-01A', 'TCGA-ZF-AA4U-01A', 'TCGA-K4-A6FZ-01A', 'TCGA-OR-A5LG-01A', 'TCGA-BH-A0HU-01A', 'TCGA-OR-A5L3-01A', 'TCGA-PK-A5HA-01A', 'TCGA-A2-A0EO-01A', 'TCGA-BH-A0H0-01A', 'TCGA-A2-A0CP-01A', 'TCGA-LL-A73Y-01A', 'TCGA-FD-A3NA-01A', 'TCGA-XF-A9SH-01A', 'TCGA-D8-A1XQ-01A', 'TCGA-FD-A43P-01A', 'TCGA-A8-A0AB-01A', 'TCGA-CF-A3MG-01A', 'TCGA-4Z-AA81-01A', 'TCGA-G2-A3IB-01A', 'TCGA-DK-A1A5-01A', 'TCGA-4Z-AA80-01A', 'TCGA-FD-A3B5-01A', 'TCGA-XF-A8HC-01A', 'TCGA-XF-A9SU-01A', 'TCGA-UY-A78L-01A', 'TCGA-FD-A3SQ-01A', 'TCGA-FD-A5C0-01A', 'TCGA-DK-A3IL-01A', 'TCGA-BT-A20T-01A', 'TCGA-XF-AAN3-01A', 'TCGA-BT-A20V-01A']


In [10]:
cnv_data

Unnamed: 0  TCGA-OR-A5KO-01A  TCGA-OR-A5KZ-01A  \
0      ENSG00000000003.13                 0                 0   
1       ENSG00000000005.5                 0                 0   
2      ENSG00000000419.11                 0                 0   
3      ENSG00000000457.12                 0                 0   
4      ENSG00000000460.15                 0                 0   
...                   ...               ...               ...   
19724   ENSG00000281873.1                 0                 1   
19725   ENSG00000281883.1                 0                 0   
19726   ENSG00000281887.1                 0                 0   
19727   ENSG00000281889.1                 0                 0   
19728   ENSG00000281899.1                 0                 0   

       TCGA-OR-A5LA-01A  TCGA-OR-A5LP-01A  TCGA-OR-A5LR-01A  TCGA-OR-A5LJ-01A  \
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
3                     0                 0                 0                 0   
4                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
19724                 0                 0                 0                 0   
19725                 0                 0                 0                 0   
19726                 0                 0                 0                 0   
19727                 0                 0                 0                 0   
19728                 0                 0                 0                 0   

       TCGA-OR-A5KY-01A  TCGA-OR-A5L9-01A  TCGA-OR-A5LH-01A  TCGA-OR-A5K9-01A  \
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
3                     0                 0                 0                 0   
4                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
19724                 0                 0                 0                -1   
19725                 0                 0                 0                 0   
19726                 0                 0                 0                 0   
19727                 0                 0                 0                 0   
19728                 0                 0                 0                 0   

       TCGA-OR-A5KT-01A  TCGA-OR-A5L3-01A  TCGA-OR-A5LB-01A  TCGA-OR-A5LK-01A  \
0                     0                 0                 0                 1   
1                     0                 0                 0                 1   
2                     0                 0                 0                 0   
3                     0                 0                 0                 0   
4                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
19724                 0                 0                 0                 0   
19725                 0                 0                 0                 0   
19726                 0                 0                 0                 0   
19727                 0                 0                 0                 0   
19728                 0                 0                 0                 0   

       TCGA-PK-A5H9-01A  TCGA-OR-A5KU-01A  TCGA-OR-A5L4-01A  TCGA-OR-A5LC-01A  \
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0             

In [11]:
# filter all the datasets
genes_col = ['xena_sample'] + samples_ids
cnv_col = ['Unnamed: 0'] + samples_ids

genes_data_filtered = genes_data[genes_col]
cnv_data_filtered = cnv_data[cnv_col]


In [12]:
ensembl_ids_gene = list(genes_data_filtered['xena_sample'])
ensembl_ids_gene = [eid.split('.')[0] for eid in ensembl_ids_gene]
mg = mygene.MyGeneInfo()
result = mg.querymany(ensembl_ids_gene, scopes='ensembl.gene', fields='symbol', species='human')
gene_symbols = {item['query']: item.get('symbol', None) for item in result}
genes_names = (list(gene_symbols.values()))
genes_data_filtered['gene name'] = genes_names
genes_data_filtered = genes_data_filtered[genes_data_filtered['gene name'].notna()]
genes_data_filtered = genes_data_filtered.drop(columns =['xena_sample'])
genes_data_filtered = genes_data_filtered.set_index('gene name')
genes_data_filtered = genes_data_filtered.transpose()


genes_data_filtered = genes_data_filtered.dropna(axis=1)
genes_data_filtered = genes_data_filtered.dropna(axis=0)

threshold = 0.5
zero_proportion = (genes_data_filtered == 0).sum() / len(genes_data_filtered)
genes_data_filtered_filtered = genes_data_filtered.loc[:, zero_proportion <= threshold]


Input sequence provided is already in string format. No operation performed
Input sequence provided is already in string format. No operation performed
22 input query terms found dup hits:	[('ENSG00000276241', 4), ('ENSG00000275496', 2), ('ENSG00000280018', 2), ('ENSG00000259182', 2), ('E
5012 input query terms found no hit:	['ENSG00000273842', 'ENSG00000264981', 'ENSG00000220993', 'ENSG00000264576', 'ENSG00000221372', 'ENS
/var/folders/83/pqwsm5cn7vscbq8l3fnf30qr0000gn/T/ipykernel_28866/1621895788.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  genes_data_filtered['gene name'] = genes_names


In [13]:
ensembl_ids_cnv = list(cnv_data_filtered['Unnamed: 0'])
ensembl_ids_cnv_clean = [eid.split('.')[0] for eid in ensembl_ids_cnv]
ensembl_ids_cnv = [eid.split('.')[0] for eid in ensembl_ids_cnv]
mg = mygene.MyGeneInfo()
result = mg.querymany(ensembl_ids_cnv, scopes='ensembl.gene', fields='symbol', species='human')
cnv_symbols = {item['query']: item.get('symbol', None) for item in result}
cnv_names = (list(cnv_symbols.values()))
cnv_data_filtered['gene name'] = cnv_names
cnv_data_filtered = cnv_data_filtered[cnv_data_filtered['gene name'].notna()]
cnv_data_filtered

cnv_data_filtered = cnv_data_filtered.drop(columns =['Unnamed: 0'])
cnv_data_filtered = cnv_data_filtered.set_index('gene name')

cnv_data_filtered = cnv_data_filtered.transpose()


Input sequence provided is already in string format. No operation performed
Input sequence provided is already in string format. No operation performed
319 input query terms found no hit:	['ENSG00000069712', 'ENSG00000112096', 'ENSG00000116957', 'ENSG00000122718', 'ENSG00000130201', 'ENS
/var/folders/83/pqwsm5cn7vscbq8l3fnf30qr0000gn/T/ipykernel_28866/2858413191.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cnv_data_filtered['gene name'] = cnv_names


In [14]:
print(cnv_data_filtered.head())

gene name         TSPAN6  TNMD  DPM1  SCYL3  FIRRM  FGR  CFH  FUCA2  GCLC  \
TCGA-B6-A0IN-01A       0     0     0      0      0    0    0      0     0   
TCGA-PK-A5HB-01A       0     0     0      0      0    0    0      0     0   
TCGA-B6-A400-01A      -1    -1     1      0      0    0    0     -1     0   
TCGA-DK-AA6S-01A       0     0     0      0      0    0    0      0     0   
TCGA-CF-A1HR-01A       0     0     0      0      0    0    0      0     0   

gene name         NFYA  STPG1  NIPAL3  LAS1L  ENPP4  SEMA3F  CFTR  ANKIB1  \
TCGA-B6-A0IN-01A     0      0       0      0      1       0    -1      -1   
TCGA-PK-A5HB-01A     0      0       0      0      0       0     0       0   
TCGA-B6-A400-01A     0      0       0      0      0       0     0       0   
TCGA-DK-AA6S-01A     0      0       0      0      0       0     0       0   
TCGA-CF-A1HR-01A     0      0       0      0      0       0     0       0   

gene name         CYP51A1  KRIT1  RAD52  BAD  LAP3  CD99  HS3ST1  AOC1  WN

In [15]:
print(genes_data_filtered_filtered.head())

gene name             RAB4B      TIGAR      RNF44      DNAH3     RPL23A  \
TCGA-B6-A0IN-01A  17.532680  16.427990  17.278451  11.174783  21.396395   
TCGA-PK-A5HB-01A  16.765502  15.660621  18.402253   7.225703  21.344480   
TCGA-B6-A400-01A  18.419916  14.852199  18.155479   9.575744  21.766022   
TCGA-DK-AA6S-01A  16.578418  17.103454  18.247500  12.721786  21.722266   
TCGA-CF-A1HR-01A  17.122040  16.902147  17.008177  10.868534  22.204521   

gene name          EHD4-AS1      ARL8B      CALB2      MFSD3  LINC00636  \
TCGA-B6-A0IN-01A  10.344979  20.169589  17.017589  19.280403   8.634311   
TCGA-PK-A5HB-01A  10.173589  19.162452  19.838833  17.123131   0.000000   
TCGA-B6-A400-01A  10.605087  19.145715  17.895519  18.973676  10.476942   
TCGA-DK-AA6S-01A   0.000000  20.032722  18.973801  17.741921  11.011189   
TCGA-CF-A1HR-01A  15.208772  20.461235  10.833588  18.054690   0.000000   

gene name              PIGV   ECE1-AS1     ZNF708  LINC01224    MYADML2  \
TCGA-B6-A0IN-01A  17.09

In [16]:
# keep only the genes in montagud nodes

genes_data_ids = list(genes_data_filtered_filtered.columns)
common_elements = list(set(genes_data_ids) & set(montagud_nodes))
genes_data_filtered = genes_data_filtered_filtered[common_elements]

print(genes_data_filtered.head())


gene name              E2F1        JUN      EEF2K       ETV1     COX4I2  \
TCGA-B6-A0IN-01A  17.343728  19.982947  16.715791  14.588991  18.170176   
TCGA-PK-A5HB-01A  18.275197  21.626910  17.614125  16.440865  18.016218   
TCGA-B6-A400-01A  17.924901  20.500199  16.467955  14.756368  15.133115   
TCGA-DK-AA6S-01A  17.773027  19.115326  17.226007  16.038720  13.877654   
TCGA-CF-A1HR-01A  18.358306  19.712882  16.828027  12.908516  16.129969   

gene name               NF1     ZBTB17       MDM2        MYC       EGFR  \
TCGA-B6-A0IN-01A  15.733077  17.335828  17.019211  18.348296  15.047397   
TCGA-PK-A5HB-01A  14.273577  18.059597  16.007789  18.940473  18.708140   
TCGA-B6-A400-01A  15.812113  16.706200  16.219231  20.897737  15.372883   
TCGA-DK-AA6S-01A  16.041003  17.783081  17.555812  16.514602  16.382868   
TCGA-CF-A1HR-01A  16.842499  16.831520  18.150301  18.101839  17.123465   

gene name             BRCA1       PTEN       BCL2      BRCA2      RUNX2  \
TCGA-B6-A0IN-01A  14.57

In [17]:
cnv_data_ids = list(cnv_data_filtered.columns)
common_elements = list(set(cnv_data_ids) & set(montagud_nodes))
cnv_data_filtered = cnv_data_filtered[common_elements]

print(cnv_data_filtered.head())

gene name         E2F1  JUN  EEF2K  ETV1  COX4I2  NF1  ZBTB17  MDM2  MYC  \
TCGA-B6-A0IN-01A     0    0      0     0       0    0       0     0    0   
TCGA-PK-A5HB-01A     0    0      0     0       0    0       0     0    0   
TCGA-B6-A400-01A     0    0      0     0       0    0      -1     0    1   
TCGA-DK-AA6S-01A     0   -1      0     0       0    0       0     0    0   
TCGA-CF-A1HR-01A     0    0      0     0       0    0       0     0    0   

gene name         EGFR  BRCA1  PTEN  BCL2  BRCA2  RUNX2  EEF2  EGF  CFLAR  \
TCGA-B6-A0IN-01A     0      1     0     0      0      1     0    0      0   
TCGA-PK-A5HB-01A     0      0     0     0      0      0     0    0      0   
TCGA-B6-A400-01A    -1      0     0     0     -1      0     0    0      0   
TCGA-DK-AA6S-01A     0      0     0     0      0      0     0    0      0   
TCGA-CF-A1HR-01A     0      0     0     0      0      0     0    0      0   

gene name         IDH1  FADD  KRAS  DAXX  YWHAZ  EP300  MED12  PDK1  APAF1  \
TC

In [18]:
 # create generic models 

folder_generic_models_cfg = 'validation/generic_models/Adeno_lung_Cancer.cfg'
folder_generic_models_bnd = 'validation/generic_models/Adeno_lung_Cancer.bnd'

folder_pers_models = 'validation/personalized_models'

patients_ids = samples_ids
tissue = 'PAN_CANCER'

create_generic_patients_cfg_bnd_validation(folder_generic_models_cfg, folder_generic_models_bnd, folder_pers_models, patients_ids, tissue)



All .cfg and .bnd files created for the validation.


In [ ]:
# personalize them 

personalized_patients_genes_cfgs(rna_seq_data, montagud_data, output_dir_resistant, output_dir_sec_resistant, patients_ids, table_rna_seq_patients, drug_interest)


In [20]:
# compute phenotype distribution

In [21]:
# compute mean for each category 

In [22]:
# create new boxplot for each category and each phenotype